In [1]:
import pandas as pd
import numpy as np
import pickle
import tensorflow as tf
from tensorflow.keras.preprocessing.text import one_hot,Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.model_selection import train_test_split
from keras.models import load_model
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding,LSTM,Dense

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [3]:
s = pd.read_csv("/content/drive/MyDrive/IMDB_Dataset.csv", on_bad_lines='skip')
s.head()

review sentiment
0  One of the other reviewers has mentioned that ...  positive
1  A wonderful little production. <br /><br />The...  positive
2  I thought this was a wonderful way to spend ti...  positive
3  Basically there's a family where a little boy ...  negative
4  Petter Mattei's "Love in the Time of Money" is...  positive

In [4]:
s["sentiment"].replace({"positive":1,"negative":0},inplace=True)
s.head()

review  sentiment
0  One of the other reviewers has mentioned that ...          1
1  A wonderful little production. <br /><br />The...          1
2  I thought this was a wonderful way to spend ti...          1
3  Basically there's a family where a little boy ...          0
4  Petter Mattei's "Love in the Time of Money" is...          1

In [5]:
x = np.array(s["review"].values)
y = np.array(s["sentiment"].values)

In [6]:
x_filtered = []

for review in x:
    review = review.lower()
    for i in review:
        punc = '''  !()-[]{};:'"\,<>./?@#$%^&*_~  '''
        if i in punc :
            review = review.replace(i, " ")
    x_filtered.append(review)
x_filtered

['one of the other reviewers has mentioned that after watching just 1 oz episode you ll be hooked  they are right  as this is exactly what happened with me  br    br   the first thing that struck me about oz was its brutality and unflinching scenes of violence  which set in right from the word go  trust me  this is not a show for the faint hearted or timid  this show pulls no punches with regards to drugs  sex or violence  its is hardcore  in the classic use of the word  br    br   it is called oz as that is the nickname given to the oswald maximum security state penitentary  it focuses mainly on emerald city  an experimental section of the prison where all the cells have glass fronts and face inwards  so privacy is not high on the agenda  em city is home to many  aryans  muslims  gangstas  latinos  christians  italians  irish and more    so scuffles  death stares  dodgy dealings and shady agreements are never far away  br    br   i would say the main appeal of the show is due to the f

In [7]:
vocalbulary_size = 5000
onehot_encoded = [one_hot(review,vocalbulary_size) for review in x_filtered]
onehot_encoded

[[4280,
  1741,
  2461,
  476,
  2339,
  2051,
  4700,
  1792,
  2886,
  4270,
  2350,
  4862,
  4031,
  2673,
  4701,
  578,
  3150,
  1185,
  3825,
  16,
  1247,
  3627,
  991,
  570,
  4188,
  4856,
  2655,
  768,
  4163,
  4565,
  4565,
  2461,
  1831,
  4663,
  1792,
  3704,
  4163,
  3970,
  4031,
  1886,
  65,
  2533,
  4643,
  1093,
  4092,
  1741,
  925,
  135,
  1442,
  1940,
  1247,
  2543,
  2461,
  908,
  1829,
  1939,
  4163,
  991,
  570,
  2113,
  4226,
  3459,
  284,
  2461,
  4621,
  1120,
  4470,
  4183,
  991,
  3459,
  3336,
  3678,
  4611,
  768,
  4065,
  1906,
  2924,
  3698,
  4470,
  925,
  65,
  570,
  3041,
  1940,
  2461,
  1028,
  3936,
  1741,
  2461,
  908,
  4565,
  4565,
  4154,
  570,
  3066,
  4031,
  3627,
  1792,
  570,
  2461,
  323,
  2568,
  1906,
  2461,
  2269,
  3662,
  3197,
  526,
  694,
  4154,
  96,
  3459,
  2545,
  2767,
  1808,
  3818,
  2009,
  474,
  1741,
  2461,
  4538,
  2050,
  583,
  2461,
  2610,
  3595,
  4709,
  4576,
  4643,

In [8]:
max_length=500
x_padded = pad_sequences(onehot_encoded,max_length,padding="post")
x_padded

array([[4280, 1741, 2461, ...,    0,    0,    0],
       [4226,   95,  624, ...,    0,    0,    0],
       [1481, 3866,  991, ...,    0,    0,    0],
       ...,
       [1481, 1818, 4226, ...,    0,    0,    0],
       [1481, 4571, 3558, ...,    0,    0,    0],
       [3678, 4280, 2836, ...,    0,    0,    0]], dtype=int32)

In [9]:
x_train,x_test,y_train,y_test = train_test_split(x_padded,y,test_size=0.2)

In [10]:
model = Sequential()
embeded_vector_size = 35
model.add(Embedding(vocalbulary_size,embeded_vector_size,input_length=max_length))
model.add(LSTM(100))
model.add(Dense(1,activation="sigmoid"))

/usr/local/lib/python3.10/dist-packages/keras/src/layers/core/embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


In [11]:
model.compile(optimizer='adam', loss='binary_crossentropy',metrics=["accuracy"])

In [12]:
model.build((None, max_length))
model.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ embedding (Embedding)                │ (None, 500, 35)             │         175,000 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ lstm (LSTM)                          │ (None, 100)                 │          54,400 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense (Dense)                        │ (None, 1)                   │             101 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 229,501 (896.49 KB)

 Trainable params: 229,501 (896.49 KB)

 Non-trainable params: 0 (0.00 B)

In [14]:
model.fit(x_train, y_train, epochs=30, validation_data=(x_test, y_test))

Epoch 1/30
2323/2323 ━━━━━━━━━━━━━━━━━━━━ 52s 22ms/step - accuracy: 0.5321 - loss: 0.6645 - val_accuracy: 0.5283 - val_loss: 0.6679
Epoch 2/30
2323/2323 ━━━━━━━━━━━━━━━━━━━━ 81s 22ms/step - accuracy: 0.5367 - loss: 0.6477 - val_accuracy: 0.5326 - val_loss: 0.6641
Epoch 3/30
2323/2323 ━━━━━━━━━━━━━━━━━━━━ 51s 22ms/step - accuracy: 0.5452 - loss: 0.6378 - val_accuracy: 0.7320 - val_loss: 0.5542
Epoch 4/30
2323/2323 ━━━━━━━━━━━━━━━━━━━━ 50s 21ms/step - accuracy: 0.8327 - loss: 0.3918 - val_accuracy: 0.8707 - val_loss: 0.3108
Epoch 5/30
2323/2323 ━━━━━━━━━━━━━━━━━━━━ 82s 22ms/step - accuracy: 0.9126 - loss: 0.2308 - val_accuracy: 0.9023 - val_loss: 0.2536
Epoch 6/30
2323/2323 ━━━━━━━━━━━━━━━━━━━━ 50s 22ms/step - accuracy: 0.9406 - loss: 0.1664 - val_accuracy: 0.9285 - val_loss: 0.2073
Epoch 7/30
2323/2323 ━━━━━━━━━━━━━━━━━━━━ 82s 22ms/step - accuracy: 0.9581 - loss: 0.1268 - val_accuracy: 0.9378 - val_loss: 0.1925
Epoch 8/30
2323/2323 ━━━━━━━━━━━━━━━━━━━━ 82s 22ms/step - accuracy: 0.9722 -

In [15]:
model.evaluate(x_test,y_test)

581/581 ━━━━━━━━━━━━━━━━━━━━ 5s 8ms/step - accuracy: 0.9617 - loss: 0.1871


[0.18160726130008698, 0.962761640548706]

In [16]:
model.save('sentiment_model.h5')

In [17]:
tokenizer = Tokenizer(num_words = 10000)
tokenizer.fit_on_texts(x_filtered)
with open('tokenizer.pkl', 'wb') as f:
    pickle.dump(tokenizer, f)

In [19]:
def get_sentiment(sentence: str):
    if not isinstance(sentence, str):
        raise ValueError("Input needs to be of type 'str'")
    sentence = sentence.lower()
    sentence = ''.join(char for char in sentence if char.isalnum() or char.isspace())
    with open('tokenizer.pkl', 'rb') as f:
        tokenizer = pickle.load(f)
    sequence = tokenizer.texts_to_sequences([sentence])
    padded_sequence = pad_sequences(sequence, maxlen=500)
    model = load_model('sentiment_model.h5')
    predicted = model.predict(padded_sequence)
    sentiment = "Positive" if predicted[0][0] > 0.5 else "Negative"
    return sentiment

print(get_sentiment("The model is powerful, but the learning curve is steep. It took me a lot of time and effort to understand how to use it effectively."))

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 111ms/step
Negative
